# Homework 3

## Description

### Data
[Reuters-21578 Text Categorization Collection Data Set](https://archive.ics.uci.edu/ml/datasets/reuters-21578+text+categorization+collection) - about 2 million instances, 28MB in size


News: 21 SGML files
We only deal with news contents inside <body> </body> tags
The other files will not be needed in this homework

### Format
One text file consisting of lines of records.

Each record contains 9 attributes separated by semicolons: 


Reuters-21578, Distribution 1.0 includes five files (all-exchanges-strings.lc.txt, all-orgs-strings.lc.txt, all-people-strings.lc.txt, all-places-strings.lc.txt, and all-topics-strings.lc.txt) which list the names of *all* legal categories in each set. A sixth file, cat-descriptions_120396.txt gives some additional information on the category sets.


### Task
4 subtasks:
+ (30pt) Given the Reuters-21578 dataset, please calculate all k-shingles and output the set representation of the text dataset as a matrix.
+ (30pt) Given the set representation, compute the minhash signatures of all documents using MapReduce.
+ (40pt) Implement the LSH algorithm by MapReduce and output the resulting candidate pairs of similar documents. 
+ (Bonus) Implement K-nearest neighbor (KNN) search using LSH and compare its performance with linear search.

## Output Format

1. Set representation:
A MxN matrix: with rows as shingles and columns as documents (N=21,578) 
2. minhash signatures:
The HxN signature matrix: with H as the number of hash functions, N=21,578
3. candidate pairs:
For each document i, there should be a list of those documents j>i with which i needs to be compared
4. comparison of KNN search an linear search


## Implementation Notes

Note the differences in rows and columns for the input data and the output matrices
* Input: rows as documents
* Output: columns as documents

Your program should be able to accept some parameters:
* k in k-shingles
* Number of hash functions H




## Implementation

In [1]:
import org.apache.spark.sql.SparkSession
import org.apache.spark.SparkContext
import org.apache.spark.SparkConf
import org.apache.hadoop.fs._
import org.apache.hadoop.conf.Configuration

import java.io.{File,PrintWriter}

  def printSample(writer: Any, data: Any, title: String = "", format: String = ""){
    println("\n"+title+" Data Sample: " + format)
    println(data+"\n")
  }

  def printSpark(writer: Any, spark: SparkSession): Unit = {
    println("Spark Entity:       " + spark)
    println("Spark version:      " + spark.version)
    println("Spark master:       " + spark.sparkContext.master)
    println("Running 'locally'?: " + spark.sparkContext.isLocal)
    println("")
  }

  def outputWriter(fileString: String): PrintWriter ={
    val outputPath = new Path(fileString)
    val outputStream = outputPath.getFileSystem(new Configuration()).create(outputPath);
    new PrintWriter(outputStream)
  }

  def getFile(fileString: String): Array[String] ={
    val inputPath = new Path(fileString)
    val inputBuffer = scala.collection.mutable.ArrayBuffer.empty[String]
    val iterator = inputPath.getFileSystem(new Configuration()).listFiles(inputPath, false)
    while(iterator.hasNext()){
        val fileStatus = iterator.next()
        if(fileStatus.isFile()){
          inputBuffer += fileStatus.getPath().toString()
        }
    }
    inputBuffer.toArray
  }


val writer = null
printSpark(writer, spark)

Spark Entity:       org.apache.spark.sql.SparkSession@4676d66
Spark version:      2.2.0
Spark master:       local[*]
Running 'locally'?: true



printSample: (writer: Any, data: Any, title: String, format: String)Unit
printSpark: (writer: Any, spark: org.apache.spark.sql.SparkSession)Unit
outputWriter: (fileString: String)java.io.PrintWriter
getFile: (fileString: String)Array[String]
writer: Null = null


In [2]:
val spark2 = spark

var data = getFile("./data")
var sample_data = Array("file:/home/micky/big_data/hw3/data/reut2-017.sgm")

spark2 = org.apache.spark.sql.SparkSession@4676d66
data = Array(file:/home/micky/big_data/hw3/data/reut2-017.sgm, file:/home/micky/big_data/hw3/data/reut2-001.sgm, file:/home/micky/big_data/hw3/data/reut2-021.sgm, file:/home/micky/big_data/hw3/data/reut2-003.sgm, file:/home/micky/big_data/hw3/data/reut2-010.sgm, file:/home/micky/big_data/hw3/data/reut2-013.sgm, file:/home/micky/big_data/hw3/data/reut2-004.sgm, file:/home/micky/big_data/hw3/data/reut2-020.sgm, file:/home/micky/big_data/hw3/data/reut2-008.sgm, file:/home/micky/big_data/hw3/data/reut2-014.sgm, file:/home/micky/big_data/hw3/data/reut2-007.sgm, file:/home/micky/big_data/hw3/data/reut2-018.sgm, file:/home/micky/big_data/hw3/data/reut2-005.sgm, file:/home/micky/big_data/hw3/dat...


[file:/home/micky/big_data/hw3/data/reut2-017.sgm, file:/home/micky/big_data/hw3/data/reut2-001.sgm, file:/home/micky/big_data/hw3/data/reut2-021.sgm, file:/home/micky/big_data/hw3/data/reut2-003.sgm, file:/home/micky/big_data/hw3/data/reut2-010.sgm, file:/home/micky/big_data/hw3/data/reut2-013.sgm, file:/home/micky/big_data/hw3/data/reut2-004.sgm, file:/home/micky/big_data/hw3/data/reut2-020.sgm, file:/home/micky/big_data/hw3/data/reut2-008.sgm, file:/home/micky/big_data/hw3/data/reut2-014.sgm, file:/home/micky/big_data/hw3/data/reut2-007.sgm, file:/home/micky/big_data/hw3/data/reut2-018.sgm, file:/home/micky/big_data/hw3/data/reut2-005.sgm, file:/home/micky/big_data/hw3/data/reut2-015.sgm, file:/home/micky/big_data/hw3/data/reut2-011.sgm, file:/home/micky/big_data/hw3/data/reut2-002.sgm, file:/home/micky/big_data/hw3/data/reut2-012.sgm, file:/home/micky/big_data/hw3/data/reut2-019.sgm, file:/home/micky/big_data/hw3/data/reut2-009.sgm, file:/home/micky/big_data/hw3/data/reut2-016.sgm,

In [3]:
import scala.collection.mutable.ListBuffer

//TODO: Sample -> Actual
var regex = """(?s)<REUTERS.*?NEWID="(\d*)".*?>.*?<TEXT.*?>(.*?)<\/TEXT>.*?<\/REUTERS>""".r
var body_regex = """(?s).*?<BODY.*?>(.*?)<\/BODY>.*?""".r
var newsParse = spark.sparkContext.emptyRDD[(Int, String)]

sample_data.map{
    path  =>
    val singleNewsParse = spark.sparkContext.wholeTextFiles(path).flatMap{
        case (_, string) =>
        val list =  ListBuffer[Tuple2[Int, String]]()
        for(m <- regex.findAllIn(string).matchData){
            for( n <- body_regex.findAllIn(m.group(2)).matchData){
                list += (Tuple2(m.group(1).toInt, n.group(1).replace("\n Reuter\n&#3;","")))
            }
        }
        list.toSeq
    }
    newsParse = newsParse.union(singleNewsParse)
}
var newsCount = newsParse.count()
print("\nCount: "+ newsCount+"\n")
printSample(writer, newsParse.take(2).mkString("\n\n"), "Parsed Sample")


Count: 940

Parsed Sample Data Sample: 
(17001,The Brazilian Coffee Institute, IBC,
plans to sell in a series of auctions over the next few weeks
robusta coffee purchased in London last year, but details of
where and when auctions will take place are still to be
finalised, IBC president Jorio Dauster told reporters.
    The sales of 630,000 bags of robusta and an unspecified
amount of Brazilian arabica coffee will take place over a
minimum of six months but it is not decided where sales will
take place or whether they will be held weekly or monthly.
    The amount offered at each sale has also not been set, but
could be in the order of 100,000 bags, Dauster said.)

(17002,AMCA International Ltd said it
appointed president and chief executive officer WIlliam Holland
to succeed Kenneth Barclay as chairman.
    Barclay, who is 60 years old, decided not to stand for
reappointment as chairman this year but will continue as a
director, AMCA said.)



regex = (?s)<REUTERS.*?NEWID="(\d*)".*?>.*?<TEXT.*?>(.*?)<\/TEXT>.*?<\/REUTERS>
body_regex = (?s).*?<BODY.*?>(.*?)<\/BODY>.*?
newsParse = UnionRDD[4] at union at <console>:59
newsCount = 940


940

### Task 1 - Calculate K-Shingle Matrix

In [4]:
def wordPreProcess(input: Any): Array[String] = {
        var matchRegex = """([$]?(?:[\w]+(?:[\w',]*[\w]+)+|[\w]))""".r
        var list =  ListBuffer[String]()
        for(m <- matchRegex.findAllIn(input.toString.toLowerCase).matchData;
          e <- m.subgroups)
          list+=e
        list.toArray
    }

wordPreProcess: (input: Any)Array[String]


In [5]:
val kShingleValue = 3
val parseSentenceRegex = """([$]?(?:[\w]+(?:[\w',]*[\w]+)+|[\w]))""".r

var flattenShingles = newsParse.flatMap{
    case (id, string)  =>
    wordPreProcess(string).sliding(kShingleValue).map{
        wordVector =>
        (wordVector.mkString(" "), id)
    }  
}
printSample(writer, flattenShingles.take(20).mkString("\n"), "Parsed Shingle Sample")


Parsed Shingle Sample Data Sample: 
(the brazilian coffee,17001)
(brazilian coffee institute,17001)
(coffee institute ibc,17001)
(institute ibc plans,17001)
(ibc plans to,17001)
(plans to sell,17001)
(to sell in,17001)
(sell in a,17001)
(in a series,17001)
(a series of,17001)
(series of auctions,17001)
(of auctions over,17001)
(auctions over the,17001)
(over the next,17001)
(the next few,17001)
(next few weeks,17001)
(few weeks robusta,17001)
(weeks robusta coffee,17001)
(robusta coffee purchased,17001)
(coffee purchased in,17001)



kShingleValue = 3
parseSentenceRegex = ([$]?(?:[\w]+(?:[\w',]*[\w]+)+|[\w]))
flattenShingles = MapPartitionsRDD[5] at flatMap at <console>:46


MapPartitionsRDD[5] at flatMap at <console>:46

In [6]:
var matrixIndex = spark.sparkContext.broadcast(newsParse.map{
    case(id, string) =>
    id.toInt
}.sortBy{
    case (id) => id
}.zipWithIndex.collectAsMap())

printSample(writer, matrixIndex.value.take(5).mkString("\n"), "Ziped With Index Sample")


Ziped With Index Sample Data Sample: 
17758 -> 719
17417 -> 411
17408 -> 402
17004 -> 3
17749 -> 711



matrixIndex = Broadcast(6)


Broadcast(6)

In [7]:
var groupedShingles = flattenShingles.groupByKey()

printSample(writer, groupedShingles.take(5).mkString("\n"), "Grouped Shingle Sample")


Grouped Shingle Sample Data Sample: 
(attacks on the,CompactBuffer(17406))
(he said and,CompactBuffer(17166, 17760, 17915))
(more than four,CompactBuffer(17422, 17644, 17871))
(improving high quality,CompactBuffer(17474))
(expire at end,CompactBuffer(17043))



groupedShingles = ShuffledRDD[11] at groupByKey at <console>:46


ShuffledRDD[11] at groupByKey at <console>:46

In [8]:
var newsCount = spark.sparkContext.broadcast(newsParse.count())
var shinglesCount = spark.sparkContext.broadcast(groupedShingles.count())
print("Count: "+shinglesCount.value+"\n")

var shingleMatrix = groupedShingles.map{
    case (text, iterable) =>
    var row = Array.fill(newsCount.value.toInt){false}
    iterable.toVector.map{
        id =>
        row(matrixIndex.value(id).toInt) = true
    }
    row
}

Count: 128427


newsCount = Broadcast(10)
shinglesCount = Broadcast(12)
shingleMatrix = MapPartitionsRDD[12] at map at <console>:52


MapPartitionsRDD[12] at map at <console>:52

In [ ]:
val shingleString = shingleMatrix.map{
      array =>
      array.map{bool => if(bool) '1' else '0'}.mkString(",")
}

shingleString.saveAsTextFile("./output/shingleMatrix")

###  Task 2 - Compute Min-Hash Signatures

In [10]:
var numOfHashFunctions = spark.sparkContext.broadcast(100)
var prime = 21601

val rand = scala.util.Random
var hashFunctionMatrix = Array.fill(numOfHashFunctions.value,2){rand.nextInt(2000) - 1000}

numOfHashFunctions = Broadcast(13)
prime = 21601
rand = scala.util.Random$@21e6639e
hashFunctionMatrix = Array(Array(186, -94), Array(646, -810), Array(336, 579), Array(185, -496), Array(-960, -333), Array(-79, -775), Array(-837, -389), Array(-5, -882), Array(623, -247), Array(306, -21), Array(-340, -233), Array(-230, 17), Array(547, 73), Array(-102, 403), Array(-583, 243), Array(-249, -35), Array(-644, 197), Array(-261, -974), Array(157, -892), Array(-140, -144), Array(843, 582), Array(88, -846), Array(-176, -391), Array(-58, -446), Array(-363, -960), Array(41, 489), Array(-303, 507), Array(982, 196), Array(-818, -542), Array(228, -236), Array(-884, 815), Array(-117, 451), Array(143, 677), Array(900, 5...


lastException: Throwable = null


[[186, -94], [646, -810], [336, 579], [185, -496], [-960, -333], [-79, -775], [-837, -389], [-5, -882], [623, -247], [306, -21], [-340, -233], [-230, 17], [547, 73], [-102, 403], [-583, 243], [-249, -35], [-644, 197], [-261, -974], [157, -892], [-140, -144], [843, 582], [88, -846], [-176, -391], [-58, -446], [-363, -960], [41, 489], [-303, 507], [982, 196], [-818, -542], [228, -236], [-884, 815], [-117, 451], [143, 677], [900, 526], [-252, 768], [769, -909], [-863, 138], [-730, 360], [-326, -617], [-604, -203], [255, 350], [-761, 944], [-718, 69], [37, 819], [-713, 8], [-298, 124], [-619, -603], [-413, 145], [297, -777], [-88, -67], [761, -532], [-557, 972], [-330, 885], [-754, 143], [970, 635], [-871, 236], [-47, -312], [912, 133], [277, 73], [636, 99], [433, -66], [293, 143], [855, 874], [-667, -756], [-291, 926], [-792, 341], [593, 749], [959, 479], [-418, 603], [-604, -246], [-9, 567], [40, 665], [-944, 994], [-280, -485], [619, 602], [-193, 630], [-272, -200], [-300, -240], [-218,

In [11]:
def hashFunction(input: Int): Array[Int] = {
//     var hashResultMatrix = Array.ofDim[String](numOfHashFunctions)
    hashFunctionMatrix.map{
        array =>
        (Math.abs(array(0).toInt * input + array(1).toInt)%prime)%newsCount.value.toInt
    }
}

hashFunction: (input: Int)Array[Int]


In [12]:
val signatureMatrix = shingleMatrix.zipWithIndex.mapPartitions{
    itr =>
    
    itr.map{
        case(rowArray, index) =>
        var matrix = Array.fill(numOfHashFunctions.value,newsCount.value.toInt){99999}
        var hashResult = hashFunction(index.toInt).toSeq
        rowArray.zipWithIndex.map{case (x,i) =>
            if(x!=false){
                for(n <- 0 until numOfHashFunctions.value){
                    matrix(n)(i) = hashResult(n)
                }
            }
        }      
        matrix
    }

}.reduce{
    case (matrix1, matrix2) =>
    for(y <- 0 until matrix1.length;
      x <- 0 until matrix1(y).length){
        if(matrix1(y)(x) > matrix2(y)(x)){
            matrix1(y)(x) = matrix2(y)(x)
        }
    }
    matrix1
}

signatureMatrix = Array(Array(2, 6, 28, 8, 2, 1, 2, 28, 17, 0, 20, 11, 0, 5, 22, 15, 12, 2, 45, 7, 22, 73, 2, 1, 11, 3, 0, 33, 8, 2, 2, 85, 2, 0, 9, 2, 12, 14, 0, 0, 2, 5, 0, 2, 2, 4, 0, 3, 4, 16, 6, 3, 28, 2, 11, 3, 1, 4, 17, 12, 22, 16, 2, 2, 0, 6, 2, 3, 2, 8, 2, 1, 1, 18, 6, 1, 3, 16, 26, 2, 2, 1, 6, 2, 2, 27, 11, 4, 0, 2, 9, 27, 0, 19, 16, 2, 7, 0, 6, 2, 3, 20, 2, 12, 40, 7, 2, 3, 16, 18, 14, 10, 8, 2, 2, 1, 33, 2, 2, 1, 17, 1, 2, 11, 10, 29, 32, 1, 14, 0, 10, 2, 9, 2, 1, 0, 1, 0, 0, 2, 2, 11, 4, 5, 4, 5, 0, 6, 0, 0, 14, 0, 6, 17, 6, 5, 0, 0, 9, 24, 28, 2, 2, 13, 11, 0, 36, 0, 2, 4, 6, 0, 7, 46, 0, 8, 8, 14, 2, 11, 1, 8, 2, 14, 3, 3, 12, 8, 0, 1, 0, 2, 2, 2, 0, 2, 0, 0, 0, 11, 2, 1, 0, 2, 23, 13, 17, 1, 2, 1, 0, 3, 10, 3, 2, 16, 1, 20, 3, 2, 5, 0, 4, 19, 35, 2, 0,...


[[2, 6, 28, 8, 2, 1, 2, 28, 17, 0, 20, 11, 0, 5, 22, 15, 12, 2, 45, 7, 22, 73, 2, 1, 11, 3, 0, 33, 8, 2, 2, 85, 2, 0, 9, 2, 12, 14, 0, 0, 2, 5, 0, 2, 2, 4, 0, 3, 4, 16, 6, 3, 28, 2, 11, 3, 1, 4, 17, 12, 22, 16, 2, 2, 0, 6, 2, 3, 2, 8, 2, 1, 1, 18, 6, 1, 3, 16, 26, 2, 2, 1, 6, 2, 2, 27, 11, 4, 0, 2, 9, 27, 0, 19, 16, 2, 7, 0, 6, 2, 3, 20, 2, 12, 40, 7, 2, 3, 16, 18, 14, 10, 8, 2, 2, 1, 33, 2, 2, 1, 17, 1, 2, 11, 10, 29, 32, 1, 14, 0, 10, 2, 9, 2, 1, 0, 1, 0, 0, 2, 2, 11, 4, 5, 4, 5, 0, 6, 0, 0, 14, 0, 6, 17, 6, 5, 0, 0, 9, 24, 28, 2, 2, 13, 11, 0, 36, 0, 2, 4, 6, 0, 7, 46, 0, 8, 8, 14, 2, 11, 1, 8, 2, 14, 3, 3, 12, 8, 0, 1, 0, 2, 2, 2, 0, 2, 0, 0, 0, 11, 2, 1, 0, 2, 23, 13, 17, 1, 2, 1, 0, 3, 10, 3, 2, 16, 1, 20, 3, 2, 5, 0, 4, 19, 35, 2, 0, 2, 2, 10, 2, 5, 11, 6, 2, 5, 1, 22, 2, 2, 2, 0, 8, 1, 2, 4, 0, 21, 2, 21, 0, 7, 3, 7, 6, 2, 0, 2, 4, 35, 2, 2, 2, 0, 17, 3, 1, 2, 2, 4, 15, 0, 24, 0, 2, 12, 0, 0, 39, 3, 0, 4, 1, 2, 2, 2, 4, 2, 0, 3, 2, 2, 2, 3, 2, 2, 4, 19, 1, 0, 8, 0, 2, 2, 2, 17,

In [13]:
val signatureString = signatureMatrix.map{
      array =>
      array.mkString(",")
}.mkString("\n")

val local_writer =  outputWriter("./output/signatureMatrix")
try {local_writer.write(signatureString)} finally {local_writer.close()}

signatureString = 


2,6,28,8,2,1,2,28,17,0,20,11,0,5,22,15,12,2,45,7,22,73,2,1,11,3,0,33,8,2,2,85,2,0,9,2,12,14,0,0,2,5,0,2,2,4,0,3,4,16,6,3,28,2,11,3,1,4,17,12,22,16,2,2,0,6,2,3,2,8,2,1,1,18,6,1,3,16,26,2,2,1,6,2,2,27,11,4,0,2,9,27,0,19,16,2,7,0,6,2,3,20,2,12,40,7,2,3,16,18,14,10,8,2,2,1,33,2,2,1,17,1,2,11,10,29,32,1,14,0,10,2,9,2,1,0,1,0,0,2,2,11,4,5,4,5,0,6,0,0,14,0,6,17,6,5,0,0,9,24,28,2,2,13,11,0,36,0,2,4,6,0,7,46,0,8,8,14,2,11,1,8,2,14,3,3,12,8,0,1,0,2,2,2,0,2,0,0,0,11,2,1,0,2,23,13,17,1,2,1,0,3,10,3,2,16,1,20,3,2,5,0,4,19,35,2,0,2,2,10,2,5,11,6,2,5,1,22,2,2,2,0,8,1,2,4,0,21,2,21,0,7,3,7,6,2,0,2,4,35,2,2,2,0,17,3,1,2,2,4,15,0,24,0,2,12,0,0,39,3,0,4,1,2,2,2,4,2,0,3,2,2,2,3,2,2,4,19,1,0,8,0,2,2,2,17,0,35,7,5,2,6,2,19,1,3,0,2,2,0,3,6,1,0,4,1,9,3,0,2,22,6,0,0,1,10,28,22,1,14,18,...


2,6,28,8,2,1,2,28,17,0,20,11,0,5,22,15,12,2,45,7,22,73,2,1,11,3,0,33,8,2,2,85,2,0,9,2,12,14,0,0,2,5,0,2,2,4,0,3,4,16,6,3,28,2,11,3,1,4,17,12,22,16,2,2,0,6,2,3,2,8,2,1,1,18,6,1,3,16,26,2,2,1,6,2,2,27,11,4,0,2,9,27,0,19,16,2,7,0,6,2,3,20,2,12,40,7,2,3,16,18,14,10,8,2,2,1,33,2,2,1,17,1,2,11,10,29,32,1,14,0,10,2,9,2,1,0,1,0,0,2,2,11,4,5,4,5,0,6,0,0,14,0,6,17,6,5,0,0,9,24,28,2,2,13,11,0,36,0,2,4,6,0,7,46,0,8,8,14,2,11,1,8,2,14,3,3,12,8,0,1,0,2,2,2,0,2,0,0,0,11,2,1,0,2,23,13,17,1,2,1,0,3,10,3,2,16,1,20,3,2,5,0,4,19,35,2,0,2,2,10,2,5,11,6,2,5,1,22,2,2,2,0,8,1,2,4,0,21,2,21,0,7,3,7,6,2,0,2,4,35,2,2,2,0,17,3,1,2,2,4,15,0,24,0,2,12,0,0,39,3,0,4,1,2,2,2,4,2,0,3,2,2,2,3,2,2,4,19,1,0,8,0,2,2,2,17,0,35,7,5,2,6,2,19,1,3,0,2,2,0,3,6,1,0,4,1,9,3,0,2,22,6,0,0,1,10,28,22,1,14,18,13,3,3,7,0,0,6,10,14,2,2,1,0,8,13,1,0,2,0,0,0,1,2,2,0,0,1,0,2,2,6,4,8,1,2,1,8,1,0,2,8,2,3,19,0,3,0,2,4,1,4,2,14,1,1,3,7,49,1,2,1,1,0,1,2,1,12,2,0,0,0,0,0,7,2,8,0,3,24,3,0,2,6,2,6,1,1,10,4,9,14,1,28,15,4,22,0,19,53,21,1,2,2,0,0,2,

In [14]:
val hashFunctionString = hashFunctionMatrix.map{
      array =>
      array.mkString(",")
}.mkString("\n")

val local_writer =  outputWriter("./output/hashFunctionMatrix")
try {local_writer.write(hashFunctionString)} finally {local_writer.close()}

hashFunctionString = 


38,-9...


186,-94
646,-810
336,579
185,-496
-960,-333
-79,-775
-837,-389
-5,-882
623,-247
306,-21
-340,-233
-230,17
547,73
-102,403
-583,243
-249,-35
-644,197
-261,-974
157,-892
-140,-144
843,582
88,-846
-176,-391
-58,-446
-363,-960
41,489
-303,507
982,196
-818,-542
228,-236
-884,815
-117,451
143,677
900,526
-252,768
769,-909
-863,138
-730,360
-326,-617
-604,-203
255,350
-761,944
-718,69
37,819
-713,8
-298,124
-619,-603
-413,145
297,-777
-88,-67
761,-532
-557,972
-330,885
-754,143
970,635
-871,236
-47,-312
912,133
277,73
636,99
433,-66
293,143
855,874
-667,-756
-291,926
-792,341
593,749
959,479
-418,603
-604,-246
-9,567
40,665
-944,994
-280,-485
619,602
-193,630
-272,-200
-300,-240
-218,-13
131,937
958,-130
-230,872
-816,-939
330,-512
-979,-337
797,-882
-142,832
38,-958
-786,990
468,-296
459,-50
-271,338
344,-885
727,-972
311,-142
242,-693
946,908
-655,330
-551,681
-363,259

### Task 3 - Implement LSH

In [19]:
var rowsPerBand = spark.sparkContext.broadcast(5)
var jaccardSimilarity = spark.sparkContext.broadcast(0.8)
var bandMax = Math.ceil(numOfHashFunctions.value/rowsPerBand.value)
var bandIndexMap = spark.sparkContext.parallelize((0 until bandMax.toInt).toList)
var signatureBroadcast = spark.sparkContext.broadcast(signatureMatrix)

rowsPerBand = Broadcast(19)
jaccardSimilarity = Broadcast(20)
bandMax = 20.0
bandIndexMap = ParallelCollectionRDD[19] at parallelize at <console>:65
signatureBroadcast = Broadcast(21)


Broadcast(21)

In [20]:
var LSH_matrix = bandIndexMap.map{
    n =>
    var matrix = Array.fill(newsCount.value.toInt,newsCount.value.toInt){false}
    for(y <- 0 until newsCount.value.toInt;
      x <- (y + 1) until newsCount.value.toInt){
        var matchCounter = 0;
        for(count <- 0 until rowsPerBand.value.toInt){
            if(signatureBroadcast.value(n * rowsPerBand.value.toInt + count)(y) == signatureBroadcast.value(n * rowsPerBand.value.toInt + count)(x)){
                matchCounter += 1;
            }
        }
        if(matchCounter.toDouble/rowsPerBand.value >= jaccardSimilarity.value){
            matrix(y)(x) = true;
            matrix(x)(y) = true;
        }
    }
    matrix
}.reduce{
    case (matrix1, matrix2) =>
    for(y <- 0 until matrix1.length;
      x <- 0 until matrix1(y).length){
        if(matrix2(y)(x)){
            matrix1(y)(x) = true
        }
    }
    matrix1
}

LSH_matrix(0).take(10).foreach(println)

false
false
false
false
false
false
false
false
false
false


LSH_matrix = Array(Array(false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, ...


[[false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, fals

In [21]:
var LSH_pairs = LSH_matrix.map{
    array =>
    var list =  ListBuffer[Int]()
    array.zipWithIndex.map{
        case (v, i) =>
        if(v==true){
            list+=i
        }        
    }
    list.toSeq
}
println(LSH_pairs(9))

val LSH_String = LSH_pairs.zipWithIndex.map{
      case(array, i) =>
      (i+1) + ": " + array.mkString(",")
}.mkString("\n")

val local_writer =  outputWriter("./output/LSH_Pairs")
try {local_writer.write(LSH_String)} finally {local_writer.close()}

List(79, 168, 367)


LSH_pairs = Array(List(409, 572, 873), List(), List(425, 705, 789), List(26, 79, 90, 142, 143, 181, 197, 255, 290, 301, 367, 370, 380, 427, 463, 661, 712, 820, 830, 902, 905, 913, 923, 933), List(), List(), List(242, 273, 300, 319, 370, 485, 515, 606, 628, 811, 856), List(), List(436, 497), List(79, 168, 367), List(202), List(), List(110, 363, 396, 458, 473, 762), List(201, 401, 417, 458), List(), List(), List(171, 248, 283, 482, 808), List(22, 35, 42, 188, 190, 194, 196, 197, 198, 207, 208, 234, 236, 240, 251, 260, 263, 287, 288, 290, 294, 299, 301, 306, 319, 353, 361, 362, 368, 390, 410, 424, 427, 432, 442, 447, 449, 463, 476, 482, 487, 494, 547, 548, 593, 650, 696, 712, 737, 811, 820, 822, 860, 868, 883, 895, 896, 909, 913, 919), List(), List(105), List(128), List(),...


[List(409, 572, 873), List(), List(425, 705, 789), List(26, 79, 90, 142, 143, 181, 197, 255, 290, 301, 367, 370, 380, 427, 463, 661, 712, 820, 830, 902, 905, 913, 923, 933), List(), List(), List(242, 273, 300, 319, 370, 485, 515, 606, 628, 811, 856), List(), List(436, 497), List(79, 168, 367), List(202), List(), List(110, 363, 396, 458, 473, 762), List(201, 401, 417, 458), List(), List(), List(171, 248, 283, 482, 808), List(22, 35, 42, 188, 190, 194, 196, 197, 198, 207, 208, 234, 236, 240, 251, 260, 263, 287, 288, 290, 294, 299, 301, 306, 319, 353, 361, 362, 368, 390, 410, 424, 427, 432, 442, 447, 449, 463, 476, 482, 487, 494, 547, 548, 593, 650, 696, 712, 737, 811, 820, 822, 860, 868, 883, 895, 896, 909, 913, 919), List(), List(105), List(128), List(), List(17, 50, 58, 97, 110, 130, 149, 172, 175, 182, 188, 196, 197, 202, 230, 235, 242, 250, 285, 288, 292, 300, 301, 319, 342, 351, 352, 353, 357, 360, 361, 363, 376, 380, 390, 396, 401, 404, 412, 413, 417, 421, 422, 424, 432, 437, 441, 

103820004 Michael Fu